In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import stats
import json
from ortools.linear_solver import pywraplp

Q1

In [3]:
f = open('station_information.json')
data = json.load(f)

In [4]:
station_list = []
for i in range(len(data['data']['stations'])):
    station_list.append(data['data']['stations'][i]['station_id'])
len(station_list)

1422

In [5]:
july = pd.read_csv('201907-citibike-tripdata.csv')
df = july[july['start station id'].isin(station_list)]
df = df[df['end station id'].isin(station_list)]
print(july.shape)
print(df.shape)

(2181064, 15)
(1878296, 15)


In [97]:
df

tripduration                 starttime                  stoptime  \
1                 267  2019-07-01 00:00:05.1780  2019-07-01 00:04:32.4500   
2                2201  2019-07-01 00:00:05.2130  2019-07-01 00:36:46.7490   
3                1660  2019-07-01 00:00:08.6010  2019-07-01 00:27:48.8050   
4                 109  2019-07-01 00:00:12.1580  2019-07-01 00:02:01.5670   
5                 106  2019-07-01 00:00:12.6680  2019-07-01 00:01:59.6060   
...               ...                       ...                       ...   
2181059           644  2019-07-31 23:59:45.2950  2019-08-01 00:10:29.8640   
2181060           589  2019-07-31 23:59:52.7170  2019-08-01 00:09:42.0870   
2181061          1302  2019-07-31 23:59:52.8280  2019-08-01 00:21:35.1090   
2181062           353  2019-07-31 23:59:57.1130  2019-08-01 00:05:50.1350   
2181063           274  2019-07-31 23:59:57.4870  2019-08-01 00:04:32.2070   

         start station id              start station name  \
1                  3143.0                 5 Ave & E 78 St   
2                   317.0               E 6 St & Avenue B   
3                   249.0         Harrison St & Hudson St   
4                  3552.0             W 113 St & Broadway   
5                  3593.0                31 St & Broadway   
...                   ...                             ...   
2181059             274.0  Lafayette Ave & Fort Greene Pl   
2181060            3285.0         W 87 St & Amsterdam Ave   
2181061             331.0             Pike St & Monroe St   
2181062            3255.0                 8 Ave & W 31 St   
2181063            3459.0                 E 53 St & 3 Ave   

         start station latitude  start station longitude  end station id  \
1                     40.776321               -73.964274          3226.0   
2                     40.724537               -73.981854          3469.0   
3                     40.718710               -74.009001           369.0   
4                     40.805973               -73.964928          3538.0   
5                     40.761584               -73.925921          3592.0   
...                         ...                      ...             ...   
2181059               40.686919               -73.976682          3409.0   
2181060               40.788390               -73.974700          3356.0   
2181061               40.711731               -73.991930           309.0   
2181062               40.750585               -73.994685           482.0   
2181063               40.757632               -73.969306          3134.0   

                    end station name  end station latitude  \
1        W 82 St & Central Park West             40.782750   
2                 India St & West St             40.731814   
3              Washington Pl & 6 Ave             40.732241   
4           W 110 St & Amsterdam Ave             40.802692   
5             Crescent St & Broadway             40.763359   
...                              ...                   ...   
2181059         Bergen St & Smith St             40.686744   
2181060      Amsterdam Ave & W 66 St             40.774667   
2181061          Murray St & West St             40.714979   
2181062              W 15 St & 7 Ave             40.739355   
2181063              3 Ave & E 62 St             40.763126   

         end station longitude  bikeid    usertype  birth year  gender  \
1                   -73.971370   21458    Customer        1996       1   
2                   -73.959950   39874  Subscriber        1986       1   
3                   -74.000264   38865  Subscriber        1988       1   
4                   -73.962950   30256  Subscriber        1997       1   
5                   -73.928647   16875  Subscriber        1988       1   
...                        ...     ...         ...         ...     ...   
2181059             -73.990632   19018  Subscriber        1964       1   
2181060             -73.984706   15330  Subscriber        1997       1   
2181061             -74.013

Q2

In [98]:
df['start_hour'] = pd.to_datetime(df['starttime']).dt.hour
df['start_weekday'] = pd.to_datetime(df['starttime']).dt.dayofweek 
df['end_hour'] = pd.to_datetime(df['stoptime']).dt.hour
df['end_weekday'] = pd.to_datetime(df['stoptime']).dt.dayofweek
new_df = df[['start station id','end station id','start_hour','start_weekday','end_hour','end_weekday','start station latitude','start station longitude']]


In [100]:
hours = [i for i in range(5,24)]
weekdays = [i for i in range(5)]
limit_df = new_df[new_df['start_hour'].isin(hours)]
limit_df = limit_df[limit_df['start_weekday'].isin(weekdays)]
limit_df.shape[0]
# limit_df.reset_index(inplace = True)
limit_df

start station id  end station id  start_hour  start_weekday  \
1511               3314.0          3538.0           5              0   
1515               3118.0          3127.0           5              0   
1516               3351.0           507.0           5              0   
1518                402.0           336.0           5              0   
1519               3459.0           164.0           5              0   
...                   ...             ...         ...            ...   
2181059             274.0          3409.0          23              2   
2181060            3285.0          3356.0          23              2   
2181061             331.0           309.0          23              2   
2181062            3255.0           482.0          23              2   
2181063            3459.0          3134.0          23              2   

         end_hour  end_weekday  start station latitude  \
1511            5            0               40.793770   
1515            5            0               40.735550   
1516            5            0               40.786995   
1518            5            0               40.740343   
1519            5            0               40.757632   
...           ...          ...                     ...   
2181059         0            3               40.686919   
2181060         0            3               40.788390   
2181061         0            3               40.711731   
2181062         0            3               40.750585   
2181063         0            3               40.757632   

         start station longitude  
1511                  -73.971888  
1515                  -73.952840  
1516                  -73.941648  
1518                  -73.989551  
1519                  -73.969306  
...                          ...  
2181059               -73.976682  
2181060               -73.974700  
2181061               -73.991930  
2181062               -73.994685  
2181063               -73.969306  

[1417865 rows x 8 columns]

In [8]:
start_end = limit_df['start station id'].append(limit_df['end station id'])
station_ids = sorted(start_end.unique())
len(station_ids)

741

In [9]:
# total_bike = np.zeros((19,len(station_ids)))
# for i in range(5,24):
#     hour_df = limit_df[limit_df['start_hour'] == i]
#     for j in range(len(station_ids)):
#         for z in range(hour_df.shape[0]):
#             if hour_df.iloc[z,0] == station_ids[j]:
#                 total_bike[i][j] += 1
# #there are 23 weekdays
# total_bike = total_bike/23
# total_bike
    

In [10]:
#miu
total_bike = np.zeros((19,len(station_ids)))
for i in range(5,24):
    hour_df = limit_df[limit_df['start_hour'] == i]
    for j in range(hour_df.shape[0]):
            if hour_df.iloc[j,0] in station_ids:
                total_bike[i-5][station_ids.index(hour_df.iloc[j,0])] += 1
#there are 23 weekdays
total_bike = total_bike/23
total_bike
    

array([[ 1.2173913 ,  0.30434783,  0.30434783, ...,  0.04347826,
         0.04347826,  0.04347826],
       [ 3.60869565,  1.08695652,  1.08695652, ...,  0.04347826,
         0.39130435,  0.        ],
       [10.26086957,  3.30434783,  2.39130435, ...,  0.73913043,
         0.47826087,  0.26086957],
       ...,
       [ 4.08695652,  3.08695652,  1.95652174, ...,  0.34782609,
         0.34782609,  0.69565217],
       [ 3.13043478,  2.34782609,  2.26086957, ...,  0.39130435,
         0.2173913 ,  0.91304348],
       [ 2.30434783,  1.47826087,  0.82608696, ...,  0.17391304,
         0.13043478,  0.7826087 ]])

In [72]:
np.mean(total_bike)

4.378599641155344

Q3

In [11]:
#p(i,j)
full_matrix = []
for i in range(5,24):
    trans_matrix = []
    hour_df = limit_df[limit_df['start_hour'] == i]
    for start in station_ids:
        if start in hour_df['start station id'].tolist():
            start_df = hour_df[hour_df['start station id'] == start]
            total = start_df.shape[0]
            l=[]
            for end in station_ids:
                end_df = start_df[start_df['end station id'] == end]
                l.append(end_df.shape[0]/total)
            trans_matrix.append(l)
        else:
            l = [0 for j in range(len(station_ids))]
            l[station_ids.index(start)] = 1
            trans_matrix.append(l)
    full_matrix.append(trans_matrix)
    print(trans_matrix)
print(full_matrix)

[[0.03571428571428571, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.03571428571428571, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.03571428571428571, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.03571428571428571, 0.0, 0.0, 0.0, 0.0, 0.0,

[[0.024096385542168676, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.024096385542168676, 0.024096385542168676, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.024096385542168676, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.04819277108433735, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.012048192771084338, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.03614457831325301, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.012048192771084338, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.012048192771084338, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Q4

In [12]:
#lambda(i)
lambda_list = []
for i in range(len(station_ids)):
    sum_list = []
    for j in range(19):
        product = []
        for z in range(len(station_ids)):
            product.append(total_bike[j][z]*full_matrix[j][z][i])
        sum_list.append(sum(product))
    lambda_list.append(sum_list)
lambda_list

[[1.3913043478260867,
  2.521739130434783,
  6.2608695652173925,
  9.608695652173905,
  13.739130434782604,
  6.56521739130435,
  6.5652173913043566,
  6.652173913043486,
  6.478260869565227,
  8.21739130434783,
  6.695652173913048,
  8.478260869565224,
  14.260869565217373,
  15.434782608695642,
  9.173913043478258,
  7.7391304347826155,
  6.478260869565223,
  5.173913043478267,
  3.6521739130434794],
 [1.0,
  1.5217391304347823,
  4.391304347826089,
  9.173913043478265,
  10.391304347826088,
  5.173913043478266,
  5.04347826086957,
  3.8695652173913073,
  5.2173913043478315,
  4.347826086956524,
  4.826086956521743,
  5.391304347826096,
  7.608695652173921,
  8.08695652173914,
  5.347826086956527,
  3.3913043478260883,
  1.956521739130434,
  1.4782608695652173,
  1.2173913043478257],
 [0.6086956521739131,
  0.3913043478260869,
  1.3043478260869563,
  4.130434782608697,
  3.6956521739130457,
  2.1304347826086953,
  1.739130434782608,
  1.7826086956521732,
  1.8260869565217384,
  2.956

Part 2

In [81]:
station_list = []
for i in range(len(data['data']['stations'])):
    station_list.append(data['data']['stations'][i]['station_id'])
print(len(station_list))
# x(0) = decision variable
capacity_list = []
for i in range(len(data['data']['stations'])):
    capacity_list.append(data['data']['stations'][i]['capacity'])
print(len(station_list))

1422
1422


In [82]:
res = {}
for key in station_list:
    for value in capacity_list:
        res[key] = value
        capacity_list.remove(value)
        break  
res

{'72': 55,
 '79': 33,
 '82': 27,
 '83': 62,
 '116': 50,
 '119': 53,
 '120': 19,
 '127': 31,
 '128': 56,
 '143': 24,
 '144': 58,
 '146': 39,
 '150': 56,
 '151': 33,
 '152': 49,
 '153': 63,
 '157': 23,
 '161': 35,
 '164': 47,
 '168': 47,
 '173': 70,
 '174': 35,
 '212': 60,
 '216': 37,
 '217': 39,
 '223': 33,
 '224': 34,
 '228': 55,
 '229': 23,
 '232': 52,
 '236': 51,
 '237': 39,
 '238': 31,
 '239': 31,
 '241': 23,
 '242': 46,
 '244': 31,
 '245': 79,
 '247': 79,
 '248': 91,
 '249': 27,
 '250': 40,
 '251': 27,
 '252': 33,
 '254': 47,
 '257': 79,
 '258': 23,
 '259': 39,
 '260': 33,
 '261': 41,
 '262': 24,
 '264': 27,
 '265': 35,
 '267': 78,
 '268': 27,
 '270': 28,
 '274': 31,
 '275': 19,
 '276': 25,
 '278': 19,
 '280': 0,
 '281': 66,
 '282': 27,
 '284': 51,
 '285': 53,
 '289': 19,
 '291': 20,
 '293': 54,
 '295': 24,
 '297': 77,
 '298': 35,
 '301': 58,
 '302': 37,
 '303': 67,
 '304': 35,
 '305': 33,
 '307': 31,
 '308': 48,
 '309': 41,
 '310': 66,
 '311': 31,
 '312': 33,
 '313': 55,
 '315': 2

In [83]:
# solver = pywraplp.Solver.CreateSolver('Case3', 'CBC')
# #.Solver.GLOP_LINEAR_PROGRAMMING or CLP_LINEAR_PROGRAMMING
# # or CBC_MIXED_INTEGER_PROGRAMMING

# objective=solver.Objective()
# objective.SetMinimization()

# #x_0 variable
# x = [None] * 19
# y = [None] * 19

# infinity = solver.infinity()
# for i in range(19):
#     x[i] = solver.IntVar(0, infinity, 'x[{}]'.format(i))
#     y[i] = solver.IntVar(0, infinity, 'y[{}]'.format(i))

# #constrains
# outage = []
# for i in range(len(station_ids)):
#     y_list = []
#     for j in range(18):
#         lam = lambda_list[i][j]
#         miu = total_bike[j][i]
#         d = res[str(station_ids[i])]
#         solver.Add(x[i+1] = x[i] + lam - miu)
#         solver.Add(y[i+1] = max(0,x[i] + lam - miu - d) + max(0, -(x[i] + lam - miu)))
#         y_list.append(y[j+1])
#     outage.append(sum(y_list))

# solver.Minimize(sum(outage))
    

In [84]:
net_inflow = [[0 for i in range(19)] for j in range(len(station_ids))]
for i in range(len(station_ids)):
    for j in range(19):
        net_inflow[i][j] = lambda_list[i][j] - total_bike[j][i]

In [85]:
optimal_initial_bike = []
optimal_current_bike = []
optimal_outages = []
for i in range(len(station_ids)):
    station_capacity = res[str(int(station_ids[i]))]
    initial_bikes = np.linspace(0, station_capacity+1, station_capacity+1) # initial bikes can be 0, 1, ..., capacity
    outages = np.zeros(station_capacity+1) # Contains number of outages as a function of the initial bikes
    current_bikes = np.copy(initial_bikes)
    for j in range(19):
        outages += np.maximum(0, current_bikes + net_inflow[i][j] - station_capacity) # Outages when exceed capacity
        outages += np.maximum(0, -(current_bikes + net_inflow[i][j])) # Outages when drop below zero
        current_bikes += net_inflow[i][j]
        current_bikes = np.maximum(current_bikes, 0) # Now pin the inventory to be >= 0, <= station capacity
        current_bikes = np.minimum(current_bikes, station_capacity)
    initial = initial_bikes[np.argmin(outages)] 
    optimal_initial_bike.append(initial)
    optimal_current_bike.append(current_bikes[initial_bikes.tolist().index(initial)])
    optimal_outages.append(min(outages))
print(sum(optimal_initial_bike))
print(sum(optimal_current_bike))
print(sum(optimal_outages))
print(np.mean(optimal_outages))


5640.410118715889
5467.232878831566
2555.8623323822667
3.4492069262918585


In [93]:
current_outages = []
for i in range(len(station_ids)):
    station_capacity = res[str(int(station_ids[i]))]
    initial_bikes = station_capacity/2 # initial bikes can be 0, 1, ..., capacity
    outages = np.zeros(1) # Contains number of outages as a function of the initial bikes
    current_bikes = np.copy(initial_bikes)
    for j in range(9,10):
        outages += np.maximum(0, current_bikes + net_inflow[i][j] - station_capacity) # Outages when exceed capacity
        outages += np.maximum(0, -(current_bikes + net_inflow[i][j])) # Outages when drop below zero
        current_bikes += net_inflow[i][j]
        current_bikes = np.maximum(current_bikes, 0) # Now pin the inventory to be >= 0, <= station capacity
        current_bikes = np.minimum(current_bikes, station_capacity)
    current_outages.append(outages)
# adding one
adding_one_outages = []
for i in range(len(station_ids)):
    station_capacity = res[str(int(station_ids[i]))]
    initial_bikes = station_capacity/2 + 1 # initial bikes can be 0, 1, ..., capacity
    outages = np.zeros(1) # Contains number of outages as a function of the initial bikes
    current_bikes = np.copy(initial_bikes)
    for j in range(9,10):
        outages += np.maximum(0, current_bikes + net_inflow[i][j] - station_capacity) # Outages when exceed capacity
        outages += np.maximum(0, -(current_bikes + net_inflow[i][j])) # Outages when drop below zero
        current_bikes += net_inflow[i][j]
        current_bikes = np.maximum(current_bikes, 0) # Now pin the inventory to be >= 0, <= station capacity
        current_bikes = np.minimum(current_bikes, station_capacity)
    adding_one_outages.append(outages)
reducing_one_outages = []
for i in range(len(station_ids)):
    station_capacity = res[str(int(station_ids[i]))]
    initial_bikes = station_capacity/2 - 1 # initial bikes can be 0, 1, ..., capacity
    outages = np.zeros(1) # Contains number of outages as a function of the initial bikes
    current_bikes = np.copy(initial_bikes)
    for j in range(9,10):
        outages += np.maximum(0, current_bikes + net_inflow[i][j] - station_capacity) # Outages when exceed capacity
        outages += np.maximum(0, -(current_bikes + net_inflow[i][j])) # Outages when drop below zero
        current_bikes += net_inflow[i][j]
        current_bikes = np.maximum(current_bikes, 0) # Now pin the inventory to be >= 0, <= station capacity
        current_bikes = np.minimum(current_bikes, station_capacity)
    reducing_one_outages.append(outages)


In [95]:
adding = []
reducting = []
for i in range(len(current_outages)):
    if current_outages[i] - adding_one_outages[i] > 0:
        adding.append(i)
        print("adding one works at " + str(i))
    if current_outages[i] - reducing_one_outages[i] > 0:
        print("reducing one works at " + str(i))
        reducting.append(i)



reducing one works at 56
reducing one works at 148
adding one works at 188
adding one works at 331
reducing one works at 389
reducing one works at 394


In [103]:
reducting

[56, 148, 389, 394]

In [107]:
latlon_add = []
for i in adding:
    position_df = limit_df[limit_df['start station id'] == station_ids[i]]
    lat = position_df.iloc[0,6]
    lon = position_df.iloc[0,7]
    latlon_add.append((lat,lon))
print(latlon_add)

latlon_reducting = []
for i in reducing:
    position_df = limit_df[limit_df['start station id'] == station_ids[i]]
    lat = position_df.iloc[0,6]
    lon = position_df.iloc[0,7]
    latlon_reducting.append((lat,lon))
print(latlon_reducing)


[(40.7652654, -73.98192338), (40.76350532, -73.97109243)]
[(40.73331967, -73.99510132), (40.72066442, -73.98517977), (40.78307, -73.95939), (40.778301, -73.9488134)]


In [22]:
latlon_add = [(40.7652654, -73.98192338), (40.76350532, -73.97109243)]
latlon_reducing = [(40.73331967, -73.99510132), (40.72066442, -73.98517977), (40.78307, -73.95939), (40.778301, -73.9488134)]

In [34]:
dfn.loc[(dfn['lon'] >= latlon_reducing[3][1]-0.001) & (dfn['lon'] <= latlon_reducing[3][1]+0.001) & (dfn['lat'] >= latlon_reducing[3][0]-0.001)& (dfn['lat'] <= latlon_reducing[3][0]+0.001), :]

name        lon        lat             x             y
566   42454196 -73.948881  40.777552 -8.231952e+06  4.979586e+06
1092  42445748 -73.948425  40.778177 -8.231901e+06  4.979678e+06
2111  42436551 -73.947967  40.778809 -8.231850e+06  4.979771e+06

In [39]:
target1 = [42428328,42445953,42449067,42432075,42454189,42454196]

In [59]:
# x = [[0 for i in range(19)] for j in range(len(station_ids))]
# y = [[0 for i in range(19)] for j in range(len(station_ids))]
# variable_1 = [[0 for i in range(19)] for j in range(len(station_ids))]
# variable_2 = [[0 for i in range(19)] for j in range(len(station_ids))]
# indicator1 = [[0 for i in range(19)] for j in range(len(station_ids))]
# indicator2 = [[0 for i in range(19)] for j in range(len(station_ids))]
# infinity = solver.infinity()
# for i in range(len(x)): #741
#     for j in range(len(x[0])): #19
#         x[i][j] = solver.IntVar(0, solver.infinity(), "x_"+str(i)+","+str(j))
#         y[i][j] = solver.IntVar(0, solver.infinity(), "x_"+str(i)+","+str(j))
#         indicator1[i][j] = solver.IntVar(0, 1, "indicator1_"+str(i)+","+str(j))
#         indicator2[i][j] = solver.IntVar(0, 1, "indicator2_"+str(i)+","+str(j))
#         variable_1[i][j] = solver.NumVar(0, solver.infinity(), "variable_1"+str(i)+","+str(j))
#         variable_2[i][j] = solver.NumVar(0, solver.infinity(), "variable_2"+str(i)+","+str(j))
        
# #constrains
# outage = []
# for i in range(len(station_ids)):
#     y_list = []
#     for j in range(18):
#         lam = lambda_list[i][j]
#         miu = total_bike[j][i]
#         d = res[str(int(station_ids[i]))]
#         solver.Add(x[i][j+1] == x[i][j] + lam - miu)
        
#         solver.Add(variable_1[i][j] <= x[i][j] + lam - miu - d + (1 - indicator1[i][j]) * 10000000)
#         solver.Add(variable_1[i][j] >= x[i][j] + lam - miu - d - (1 - indicator1[i][j]) * 10000000)
#         solver.Add(variable_1[i][j] <= indicator1[i][j] * 10000000)
#         solver.Add(x[i][j] + lam - miu - d <= indicator1[i][j] * 10000000)
        
#         solver.Add(variable_2[i][j] <= (-(x[i][j] + lam - miu)) + (1 - indicator2[i][j]) * 10000000)
#         solver.Add(variable_2[i][j] >= (-(x[i][j] + lam - miu)) - (1 - indicator2[i][j]) * 10000000)
#         solver.Add(variable_2[i][j] <= indicator2[i][j] * 10000000)
#         solver.Add((-(x[i][j] + lam - miu)) <= indicator2[i][j] * 10000000)
        
#         solver.Add(y[i][j+1] == variable_1[i][j] + variable_2[i][j])
#         y_list.append(y[i][j+1])
#     outage.append(sum(y_list))
# solver.Minimize(sum(outage))        


In [ ]:
# #find the optimal solution by solver
# status = solver.Solve()
# if status == solver.OPTIMAL:
#     print("Solver reaches the optimal solution with objective function = " + str(objective.Value()))

# else:
#     print('Solver cannot find optimal solution')